In [1]:
from confluent_kafka import Consumer
from confluent_kafka.serialization import SerializationContext, MessageField
from confluent_kafka.schema_registry.json_schema import JSONDeserializer
from confluent_kafka.schema_registry import SchemaRegistryClient,Schema
import pymongo
from pymongo import MongoClient

In [2]:
#CONFIGURATION DETAILS

API_KEY = 'LAMZT52YQ3KXOLCK'
ENDPOINT_SCHEMA_URL  = 'https://psrc-nx65v.us-east-2.aws.confluent.cloud'
API_SECRET_KEY = 'M9R2ELFp/CYUUc56U1H1vbsKyse1EtCNrR3qqGUpQ7F72gCRT62Lc5+jWpLid1oB'
BOOTSTRAP_SERVER = 'pkc-921jm.us-east-2.aws.confluent.cloud:9092'
SECURITY_PROTOCOL = 'SASL_SSL'
SSL_MACHENISM = 'PLAIN'
SCHEMA_REGISTRY_API_KEY = 'T6UDFASJDL3RKCWZ'
SCHEMA_REGISTRY_API_SECRET = 'KQNwg+/HbCglNBys5AeK542yYObZCV7IbYj1w0Fxo3E1sOQd3UZ1pzaTAYUQ+/Db'

In [3]:
#CONFIGURATION FUNCTIONS

def sasl_conf():

    sasl_conf = {'sasl.mechanism': SSL_MACHENISM,
                 # Set to SASL_SSL to enable TLS support.
                #  'security.protocol': 'SASL_PLAINTEXT'}
                'bootstrap.servers':BOOTSTRAP_SERVER,
                'security.protocol': SECURITY_PROTOCOL,
                'sasl.username': API_KEY,
                'sasl.password': API_SECRET_KEY
                }
    return sasl_conf



def schema_config():
    return {'url':ENDPOINT_SCHEMA_URL,
    
    'basic.auth.user.info':f"{SCHEMA_REGISTRY_API_KEY}:{SCHEMA_REGISTRY_API_SECRET}"

    }

In [4]:
def main(topic):

    schema_registry_conf = schema_config()
    schema_registry_client = SchemaRegistryClient(schema_registry_conf)
#     schema = Schema(schema_str, 'JSON')
#     print(schema_registry_client.register_schema('case-value', schema, normalize_schemas=False))
    latest_version = schema_registry_client.get_latest_version(topic+'-value')
    json_deserializer = JSONDeserializer(latest_version.schema)

    consumer_conf = sasl_conf()
    consumer_conf.update({
                     'group.id': 'group1',
                     'auto.offset.reset': "earliest"})

    consumer = Consumer(consumer_conf)
    consumer.subscribe([topic])
    list_of_dict = []
    
    
    
    while True:
        try:
            # SIGINT can't be handled when polling, limit timeout to 1 second.
            msg = consumer.poll(1.0)
            if msg is None:
                continue

            dic = json_deserializer(msg.value(), SerializationContext(msg.topic(), MessageField.VALUE))
            list_of_dict.append(dic)

            if dic is not None:
                print("User record {}: car: {}\n"
                      .format(msg.key(), dic))
        except KeyboardInterrupt:
            break
    return list_of_dict

    consumer.close()


In [5]:
restaurants = main('restaurants')

User record b'581087c5-2717-49c0-9108-f01fcd4e4934': car: {'Order Number': 16117, 'Order Date': '03/08/2019 20:17', 'Item Name': 'Lamb Tikka', 'Quantity': 1, 'Product Price': 4.95, 'Total products': 7}

User record b'61febf43-a93a-444b-9d7d-208aff93a1d7': car: {'Order Number': 16115, 'Order Date': '03/08/2019 20:01', 'Item Name': 'Peshwari Naan', 'Quantity': 1, 'Product Price': 2.95, 'Total products': 7}

User record b'6948c2d4-c93a-49ff-a26c-86ce5cc0dd6d': car: {'Order Number': 16111, 'Order Date': '03/08/2019 19:29', 'Item Name': 'Peshwari Naan', 'Quantity': 1, 'Product Price': 2.95, 'Total products': 4}

User record b'7d4d756a-b83d-4194-96b8-1d41e0feeb43': car: {'Order Number': 16110, 'Order Date': '03/08/2019 19:28', 'Item Name': 'Tandoori Chicken Masala', 'Quantity': 1, 'Product Price': 8.95, 'Total products': 8}

User record b'9873d497-669f-49d8-a001-20cd6a9388e1': car: {'Order Number': 16109, 'Order Date': '03/08/2019 19:26', 'Item Name': 'Chicken Tikka Masala', 'Quantity': 1, '

User record b'16ceb04c-6dd4-4388-a17e-4c896f65bc75': car: {'Order Number': 12910, 'Order Date': '12/01/2019 18:55', 'Item Name': 'Mint Sauce', 'Quantity': 1, 'Product Price': 0.5, 'Total products': 8}

User record b'39f1b985-5428-47fc-9f1a-a0be7b851c18': car: {'Order Number': 12895, 'Order Date': '11/01/2019 18:48', 'Item Name': 'Lime Pickle', 'Quantity': 1, 'Product Price': 0.5, 'Total products': 9}

User record b'9bc44ef7-1087-4eba-a6ad-a9528bf1665a': car: {'Order Number': 12842, 'Order Date': '05/01/2019 19:39', 'Item Name': 'Mint Sauce', 'Quantity': 6, 'Product Price': 0.5, 'Total products': 15}

User record b'a1686a55-b1f2-4017-a8cc-058e02d22ada': car: {'Order Number': 12828, 'Order Date': '05/01/2019 18:08', 'Item Name': 'Mango Chutney', 'Quantity': 2, 'Product Price': 0.5, 'Total products': 7}

User record b'd0ca211c-d502-4097-9e96-51aeabe5fede': car: {'Order Number': 12825, 'Order Date': '05/01/2019 17:43', 'Item Name': 'Mango Chutney', 'Quantity': 1, 'Product Price': 0.5, 'Tot

User record b'49228de0-a93a-4dfa-aaa7-9a3cb7e08018': car: {'Order Number': 9339, 'Order Date': '23/04/2018 18:21', 'Item Name': 'Mango Chutney', 'Quantity': 1, 'Product Price': 0.5, 'Total products': 16}

User record b'aa4cce53-0471-4219-a09b-55d70a542c63': car: {'Order Number': 9339, 'Order Date': '23/04/2018 18:21', 'Item Name': 'Red Sauce', 'Quantity': 2, 'Product Price': 0.5, 'Total products': 16}

User record b'a47de3d4-6ecd-4ab7-8867-ef338d6ed9d6': car: {'Order Number': 9312, 'Order Date': '21/04/2018 22:56', 'Item Name': 'Onion Chutney', 'Quantity': 1, 'Product Price': 0.5, 'Total products': 4}

User record b'a73a214e-41df-492a-b0af-ce3804c90d38': car: {'Order Number': 9304, 'Order Date': '21/04/2018 20:01', 'Item Name': 'Mint Sauce', 'Quantity': 1, 'Product Price': 0.5, 'Total products': 11}

User record b'e15c608a-ebe3-4371-96f4-c2b205525c7f': car: {'Order Number': 9302, 'Order Date': '21/04/2018 19:39', 'Item Name': 'Mango Chutney', 'Quantity': 1, 'Product Price': 0.5, 'Total

User record b'84aef474-4b53-42f2-8f8f-d35c730cae87': car: {'Order Number': 3644, 'Order Date': '08/11/2016 17:53', 'Item Name': 'Red Sauce', 'Quantity': 1, 'Product Price': 0.5, 'Total products': 10}

User record b'e91c7f87-866e-49c8-90d9-a4be0aa2fed7': car: {'Order Number': 3617, 'Order Date': '05/11/2016 19:27', 'Item Name': 'Mint Sauce', 'Quantity': 1, 'Product Price': 0.5, 'Total products': 5}

User record b'f0b529f7-6c6f-4498-b44f-2563f77ce165': car: {'Order Number': 3595, 'Order Date': '03/11/2016 18:48', 'Item Name': 'Mango Chutney', 'Quantity': 1, 'Product Price': 0.5, 'Total products': 8}

User record b'f9aa6a83-45fe-4469-8382-a930a95ea2e9': car: {'Order Number': 3568, 'Order Date': '30/10/2016 18:19', 'Item Name': 'Mint Sauce', 'Quantity': 1, 'Product Price': 0.5, 'Total products': 11}

User record b'8fc55b2a-5d7c-4ec9-ad40-7174071e0b36': car: {'Order Number': 3552, 'Order Date': '29/10/2016 17:45', 'Item Name': 'Mint Sauce', 'Quantity': 1, 'Product Price': 0.5, 'Total produc

User record b'a0086c82-3d33-4d2a-aa2c-208989d08586': car: {'Order Number': 13744, 'Order Date': '09/03/2019 18:00', 'Item Name': 'Plain Naan', 'Quantity': 1, 'Product Price': 2.6, 'Total products': 11}

User record b'96234e38-3b1b-4ece-a777-cfe514e079cc': car: {'Order Number': 13736, 'Order Date': '08/03/2019 19:23', 'Item Name': 'Plain Naan', 'Quantity': 1, 'Product Price': 2.6, 'Total products': 5}

User record b'af23dfa9-3f87-4da4-850e-dcca382ad6bb': car: {'Order Number': 13713, 'Order Date': '07/03/2019 19:34', 'Item Name': 'Plain Naan', 'Quantity': 1, 'Product Price': 2.6, 'Total products': 5}

User record b'946f34d0-6b78-4510-9c90-102f97d56425': car: {'Order Number': 13677, 'Order Date': '03/03/2019 18:22', 'Item Name': 'Plain Naan', 'Quantity': 2, 'Product Price': 2.6, 'Total products': 4}

User record b'8f58ff02-ec73-4750-97fe-4a1da81a5d0a': car: {'Order Number': 13662, 'Order Date': '02/03/2019 19:55', 'Item Name': 'Plain Naan', 'Quantity': 1, 'Product Price': 2.6, 'Total prod

...

User record b'a941a46a-4f8f-49c0-a04a-1ffcd5978083': car: {'Order Number': 4869, 'Order Date': '24/03/2017 20:09', 'Item Name': 'Korma', 'Quantity': 1, 'Product Price': 8.95, 'Total products': 5}

User record b'0cf5b17b-cb35-4575-9b8c-d3a663976ee8': car: {'Order Number': 4865, 'Order Date': '24/03/2017 19:44', 'Item Name': 'Bhuna', 'Quantity': 1, 'Product Price': 8.95, 'Total products': 6}

User record b'40c2dfc6-c271-4f93-8b7e-cf4e3cca2bd9': car: {'Order Number': 4856, 'Order Date': '24/03/2017 18:36', 'Item Name': 'Pathia', 'Quantity': 1, 'Product Price': 8.95, 'Total products': 6}

User record b'0242725c-1923-4518-b3d5-5760a557b500': car: {'Order Number': 4848, 'Order Date': '22/03/2017 22:13', 'Item Name': 'Mushroom', 'Quantity': 1, 'Product Price': 8.95, 'Total products': 3}

User record b'7d1c6298-b253-468a-b52f-d38ce06eb410': car: {'Order Number': 4845, 'Order Date': '22/03/2017 12:11', 'Item Name': 'Tandoori Chicken (Main)', 'Quantity': 2, 'Product Price': 8.95, 'Total products

User record b'a7f64282-dbbd-4002-9a9d-bcd9539e334d': car: {'Order Number': 10423, 'Order Date': '25/07/2018 20:03', 'Item Name': 'Butter Chicken', 'Quantity': 1, 'Product Price': 9.95, 'Total products': 7}

User record b'3508bcca-7ac2-4dc3-95fd-6b5847996ee2': car: {'Order Number': 10413, 'Order Date': '24/07/2018 19:47', 'Item Name': 'Vegetable Biryani', 'Quantity': 1, 'Product Price': 9.95, 'Total products': 6}

User record b'a007ab44-0b11-450d-981d-7ea965765273': car: {'Order Number': 10384, 'Order Date': '21/07/2018 18:34', 'Item Name': 'Butter Chicken', 'Quantity': 1, 'Product Price': 9.95, 'Total products': 7}

User record b'2a1c41f7-ee80-42b3-8133-2b4ff7024140': car: {'Order Number': 10380, 'Order Date': '21/07/2018 18:16', 'Item Name': 'Butter Chicken', 'Quantity': 1, 'Product Price': 9.95, 'Total products': 9}

User record b'c356fe0e-9736-4d3e-9c45-fa8c9d231a3e': car: {'Order Number': 10372, 'Order Date': '20/07/2018 19:26', 'Item Name': 'Lal Mirch Chicken', 'Quantity': 1, 'Pro

User record b'a7d9d1cc-7652-44a4-9b3b-472e45f87bbb': car: {'Order Number': 2253, 'Order Date': '08/04/2016 19:24', 'Item Name': 'Chicken Rezala', 'Quantity': 1, 'Product Price': 9.95, 'Total products': 6}

User record b'f0aacbe7-659d-424a-83de-4ceb8ae48116': car: {'Order Number': 2253, 'Order Date': '08/04/2016 19:24', 'Item Name': 'Chicken Balti', 'Quantity': 1, 'Product Price': 9.95, 'Total products': 6}

User record b'988715de-2c3c-4222-8bc6-ab82850dee40': car: {'Order Number': 2244, 'Order Date': '06/04/2016 19:04', 'Item Name': 'Chicken Shashlick', 'Quantity': 1, 'Product Price': 9.95, 'Total products': 9}

User record b'c1f233b7-ee01-439f-9aa7-7409dc7fa196': car: {'Order Number': 2206, 'Order Date': '29/03/2016 20:02', 'Item Name': 'Lamb Biryani', 'Quantity': 1, 'Product Price': 9.95, 'Total products': 3}

User record b'2bbe210e-566b-4c65-8898-948ac6bd841e': car: {'Order Number': 2204, 'Order Date': '29/03/2016 18:43', 'Item Name': 'Chicken Balti', 'Quantity': 1, 'Product Price':

User record b'9c0227a1-832d-48e3-add8-b9077cc842ba': car: {'Order Number': 2630, 'Order Date': '04/06/2016 17:56', 'Item Name': 'Chicken Tikka Biryani', 'Quantity': 1, 'Product Price': 10.95, 'Total products': 8}

User record b'd675bbf8-e642-44b5-ab0d-f01a7302d51f': car: {'Order Number': 2598, 'Order Date': '30/05/2016 18:10', 'Item Name': 'Chicken Tikka Balti', 'Quantity': 1, 'Product Price': 10.95, 'Total products': 7}

User record b'05be0f8d-99fd-42be-bf0f-ffa9cf7f46e6': car: {'Order Number': 2595, 'Order Date': '30/05/2016 17:03', 'Item Name': 'Chicken Tikka Balti', 'Quantity': 1, 'Product Price': 10.95, 'Total products': 6}

User record b'19eb2441-b533-48c4-95e2-aa7835d21e35': car: {'Order Number': 2527, 'Order Date': '20/05/2016 17:56', 'Item Name': 'Chicken Tikka Balti', 'Quantity': 1, 'Product Price': 10.95, 'Total products': 9}

User record b'0401f7c1-6455-4627-9311-78b4b78e27ed': car: {'Order Number': 2503, 'Order Date': '14/05/2016 19:28', 'Item Name': 'Prawn Biryani', 'Quan

User record b'fd4f3128-f10e-455d-88c9-de3254bcc2ea': car: {'Order Number': 2814, 'Order Date': '31/07/2016 12:51', 'Item Name': 'House Red wine 75cl', 'Quantity': 1, 'Product Price': 17.95, 'Total products': 11}

User record b'344ecce0-b654-4c5b-99e6-634ac71d696d': car: {'Order Number': 2503, 'Order Date': '14/05/2016 19:28', 'Item Name': 'House Red wine 75cl', 'Quantity': 2, 'Product Price': 17.95, 'Total products': 6}



In [6]:
print(len(restaurants))

37351
